In [ ]:
import pandas as pd
import statsmodels.api as sm
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression, Ridge, Lasso
from sklearn.metrics import r2_score, mean_squared_error, mean_absolute_percentage_error

Для последующего построения предсказательных моделей нами был использован датасет, полученный по итогам проведения этапа EDA. Также сразу была определена целевая переменная - worldwide gross (кассовые сборы):

In [ ]:
df = pd.read_csv('data_after_eda.csv')
df = df.iloc[:, 1:]

target = 'worldwide_gross'

Для устранения проблемы мультиколлинеарности нами была осуществлена проверка на кросс-корреляцию между рассматриваемыми числовыми признаками: признаки, продемонстрировавшие корреляцию между собой были удалены на основании логики их расчета

In [31]:
df.select_dtypes(['int', 'float']).corr() > 0.9
df = df.drop(columns=['profit_or_loss', 'p&l_rate'])

Далее производилась предобработка категориальных переменных. Ввиду того, что в ячейках содержалось сразу несколько категорий, использовать метод get_dummies к колонкам не представлялось возможным, вследствие чего нами было принято решение сначала разделить информацию на столбцы с кодированием, а затем добавить их к исходному датасету, удалив столбцы с полным описанием всех категорий, к которым относился фильм.

In [32]:
dir = df['director'].str.strip().str.get_dummies(sep=',')
wr = df['writer'].str.strip().str.get_dummies(sep=',')
cast = df['cast'].str.strip().str.get_dummies(sep=',')
coo = df['country_of_origin'].str.strip().str.get_dummies(sep=',')
lang = df['languages'].str.strip().str.get_dummies(sep=',')
genre = df['genre'].str.strip().str.get_dummies(sep=',')

In [33]:
dir_col = ['director_' + i for i in list(dir.columns)]
dir = dir.rename(columns=dict(zip(dir.columns, dir_col)))

wr_col = ['writer_' + i for i in list(wr.columns)]
wr = wr.rename(columns=dict(zip(wr.columns, wr_col)))

cast_col = ['cast_' + i for i in list(cast.columns)]
cast = cast.rename(columns=dict(zip(cast.columns, cast_col)))

coo_col = ['coo_' + i for i in list(coo.columns)]
coo = coo.rename(columns=dict(zip(coo.columns, coo_col)))

lang_col = ['lang_' + i for i in list(lang.columns)]
lang = lang.rename(columns=dict(zip(lang.columns, lang_col)))

genre_col = ['genre_' + i for i in list(genre.columns)]
genre = genre.rename(columns=dict(zip(genre.columns, genre_col)))

In [34]:
df = df.drop(columns=['director','writer', 'cast', 'country_of_origin', 'languages','genre', 'title'])

После подготовки датасета мы разделили его на части - столбец с данными о целевой переменной и датасет с независимыми переменными (признаками)

In [ ]:
X = df.drop(columns=target)
y = df[target]

Для корректного построения модели приведем числовые признаки к единому виду с помощью функции Standard Scaler и применим ее к датасету с независимыми переменными

In [35]:
from sklearn.preprocessing import StandardScaler

scale = StandardScaler()
X_sc = scale.fit_transform(X)

In [36]:
X_sc = pd.DataFrame(data=X_sc, columns=X.columns)
X = pd.concat([X_sc, dir, wr, cast, coo, lang, genre], axis = 1)

Мы разделили выборку на тестовую и обучающую в процентном соотношении 20 к 80 и зафиксировали ее результат с помощью определения random state

In [37]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, shuffle=True, random_state = 42)

In [96]:
X_train_OLS = X_train.copy()
X_test_OLS = X_test.copy()
X_train_OLS = sm.add_constant(X_train_OLS)
X_test_OLS = sm.add_constant(X_test_OLS)
model = sm.OLS(y_train, X_train_OLS).fit()
model.summary()

/usr/local/lib/python3.11/dist-packages/statsmodels/regression/linear_model.py:1795: RuntimeWarning: divide by zero encountered in divide
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/usr/local/lib/python3.11/dist-packages/statsmodels/regression/linear_model.py:1795: RuntimeWarning: invalid value encountered in scalar multiply
  return 1 - (np.divide(self.nobs - self.k_constant, self.df_resid)
/usr/local/lib/python3.11/dist-packages/statsmodels/regression/linear_model.py:1717: RuntimeWarning: divide by zero encountered in scalar divide
  return np.dot(wresid, wresid) / self.df_resid
/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:1527: RuntimeWarning: invalid value encountered in multiply
  cov_p = self.normalized_cov_params * scale


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:        worldwide_gross   R-squared:                       1.000
Model:                            OLS   Adj. R-squared:                    nan
Method:                 Least Squares   F-statistic:                       nan
Date:                Sun, 15 Jun 2025   Prob (F-statistic):                nan
Time:                        15:11:33   Log-Likelihood:                 14849.
No. Observations:                1164   AIC:                        -2.737e+04
Df Residuals:                       0   BIC:                        -2.148e+04
Df Model:                        1163                                         
Covariance Type:            nonrobust                                         
===========================================================================================================
                                              coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------------------------------------------------------------------------
const                                     9.66e+07        inf          0        nan         nan         nan
average_rating                           4.495e+07        inf          0        nan         nan         nan
metascore                                5.589e+06        inf          0        nan         nan         nan
runtime                                  -7.85e+06        inf         -0        nan         nan         nan
budget                                   1.771e+08        inf          0        nan         nan         nan
release_year                             1.317e+07        inf          0        nan         nan         nan
lang_cnt                                 8.595e+06        inf          0        nan         nan         nan
country_cnt                              -8.79e+06        inf         -0        nan         nan         nan
coproduction                             1.277e+07        inf          0        nan         nan         nan
director_Aaron Sorkin                   -1.221e+07        inf         -0        nan         nan         nan
director_Abhishek Chaubey                3.882e+06        inf          0        nan         nan         nan
director_Adam McKay                     -2.565e+07        inf         -0        nan         nan         nan
director_Adam Shankman                  -7.934e-08        inf         -0        nan         nan         nan
director_Adrian Lyne                    -9.039e-08        inf         -0        nan         nan         nan
director_Agnieszka Holland              -1.137e-07        inf         -0        nan         nan         nan
director_Akhtem Seitablaev               5.892e-08        inf          0        nan         nan         nan
director_Akira Kurosawa                  7.269e+06        inf          0        nan         nan         nan
director_Alain Gsponer                   5.498e+06        inf          0        nan         nan         nan
director_Alan J. Pakula                  1.186e+06        inf          0        nan         nan         nan
director_Alan Parker                    -1.972e+07        inf         -0        nan         nan         nan
director_Alejandro Amenábar               1.52e+07        inf          0        nan         nan         nan
director_Alejandro G. Iñárritu          -7.311e+06        inf         -0        nan         nan         nan
director_Alejandro Jodorowsky           -3.644e+06        inf         -0        nan         nan         nan
director_Alejandro Monteverde            -8.19e+05        inf         -0        nan         nan         nan
director_Alex Garland                   -7.482e+06        inf         -0        nan         nan         nan
director_Alex Gibney                     5.446e+06        i

Далее мы построили модель линейной регрессии, обучили ее на обучающей выборке и построили предсказание на основании данных из тестовой выборки. Метрики, а именно коэффициент детерминации и среднеквадратическая ошибка, указали на то, что модель переобучилась вследствие большого количества признаков и чрезмерного подстраивания под них. На основании полученных результатов можно сделать вывод, что согласно разработанной модели наибольшую значимость (коэффициентную) для определения успеха масштабности кассовых сборов имело наличие в составе актеров Мишель Родригез, Джованни Рибиси, Стивена Ланга и Сигурни Уивер, в роли директора - Джеймса Кэмерона.

In [93]:
model = LinearRegression()
model.fit(X_train, y_train)
y_pred_train = model.predict(X_train)
y_pred_test = model.predict(X_test)
print(f'R^2 для обучающей выборки равен {r2_score(y_train, y_pred_train)}')
print(f'R^2 для тестовой выборки равен {r2_score(y_test, y_pred_test)}')
print(f'MSE для обучающей выборки равна {mean_squared_error(y_train, y_pred_train)}')
print(f'MSE для тестовой выборки равна {mean_squared_error(y_test, y_pred_test)}')
LR_res = pd.DataFrame(data=(zip(X.columns, model.coef_)), columns=['params', 'coefficients'])
display(LR_res.sort_values('coefficients', ascending=False).head(7))

R^2 для обучающей выборки равен 1.0
R^2 для тестовой выборки равен 0.6192562467965594
MSE для обучающей выборки равна 7.0967315643746206e-12
MSE для тестовой выборки равна 1.8300735149809656e+16


params  coefficients
6053  cast_ Michelle Rodriguez  3.525497e+08
4591     cast_ Giovanni Ribisi  3.231400e+08
6997        cast_ Stephen Lang  2.550895e+08
270     director_James Cameron  2.497344e+08
6926    cast_ Sigourney Weaver  2.492841e+08
8524          cast_Zoe Saldana  2.211252e+08
3548          cast_ Billy Zane  2.012614e+08

Для улучшения качества прогнозовы мы решили построить модели Ridge и Lasso,  методика действия которых основана на приписывании штрафов за некорректное отражение коэффициентов, что позволяет обнулить незначимые из независимых переменных, а также улучшить качество прогноза.

In [91]:
model = Ridge(alpha=25)
model.fit(X_train, y_train)
y_pred_train = model.predict(X_train)
y_pred_test = model.predict(X_test)
print(f'R^2 для обучающей выборки равен {r2_score(y_train, y_pred_train)}')
print(f'R^2 для тестовой выборки равен {r2_score(y_test, y_pred_test)}')
print(f'MSE для обучающей выборки равна {mean_squared_error(y_train, y_pred_train)}')
print(f'MSE для тестовой выборки равна {mean_squared_error(y_test, y_pred_test)}')
Ridge_res = pd.DataFrame(data=(zip(X.columns, model.coef_)), columns=['params', 'coefficients'])
display(Ridge_res.sort_values('coefficients', ascending=False).head(7))

R^2 для обучающей выборки равен 0.8310525445891037
R^2 для тестовой выборки равен 0.6632658021853264
MSE для обучающей выборки равна 1.0894365742288516e+16
MSE для тестовой выборки равна 1.6185382736396964e+16


params  coefficients
3                     budget  1.771520e+08
270   director_James Cameron  8.772479e+07
2463    writer_James Cameron  7.247864e+07
6926  cast_ Sigourney Weaver  6.963022e+07
6997      cast_ Stephen Lang  6.892641e+07
8524        cast_Zoe Saldana  6.631051e+07
4591   cast_ Giovanni Ribisi  5.675738e+07

In [92]:
model = Lasso(alpha=1000)
model.fit(X_train, y_train)
y_pred_train = model.predict(X_train)
y_pred_test = model.predict(X_test)
print(f'R^2 для обучающей выборки равен {r2_score(y_train, y_pred_train)}')
print(f'R^2 для тестовой выборки равен {r2_score(y_test, y_pred_test)}')
print(f'MSE для обучающей выборки равна {mean_squared_error(y_train, y_pred_train)}')
print(f'MSE для тестовой выборки равна {mean_squared_error(y_test, y_pred_test)}')
Lasso_res = pd.DataFrame(data=(zip(X.columns, model.coef_)), columns=['params', 'coefficients'])
display(Lasso_res.sort_values('coefficients', ascending=False).head(7))

/usr/local/lib/python3.11/dist-packages/sklearn/linear_model/_coordinate_descent.py:695: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 6.749e+16, tolerance: 7.506e+15
  model = cd_fast.enet_coordinate_descent(


R^2 для обучающей выборки равен 0.999986914540205
R^2 для тестовой выборки равен 0.5335662576000851
MSE для обучающей выборки равна 843799538532.2357
MSE для тестовой выборки равна 2.241948899430623e+16


params  coefficients
6053  cast_ Michelle Rodriguez  9.562587e+08
1088      writer_ Erik Sommers  9.513295e+08
374       director_Kelsey Mann  9.495694e+08
3548          cast_ Billy Zane  9.106092e+08
1233     writer_ Jack Epps Jr.  6.866318e+08
1413          writer_ Kai Bird  5.740812e+08
270     director_James Cameron  5.734722e+08

Из построенных моделей наилучшей оказалась модель Ridge: ее коэффициент детерминации в сравнении с другими моделями выше, а среднеквадратическая ошибка, наоборот ниже. Согласно полученным результатам, на целевую переменную (объем кассовых сборов) значительно воздействие оказывает бюджет фильма, а также наличие в составе сценариста и директора Джеймса Кэмерона, в составе актеров - Джованни Рибиси, Стивена Ланга, Зои Салдана и Сигурни Уивер

Таким образом, наилучшее качество продемонстрировала модель Ridge с коэффициентом детерминации для тестовой выборки в 0.66 у.ед.